# Astrofísica Computacional
## Proyecto Final: Problema Gravitacional de los N-Cuerpos

### Desarrollado por: 
### Joar Esteban Buitrago Carrillo
### Juan Sebastian Montoya Combita  

  

###Observatorio Astronómico Nacional  
2021

Las ecuaciones de movimiento de N-Partículas moviendose bajo su interacción gravitacional mutua se puede escribir en la forma.
$$m_{i}\ddot{x}_{i} = -Gm_{i} \sum_{j=1, i \neq j}^{N} \frac{m_{j}}{|x_{ij}|^{2}}$$
Donde $x_{ij}=x_{i}-x_{j}$ es el vector que apunta desde la partícula $j$ a la partícula $i$.


In [1]:
import numpy as np
import matplotlib.pyplot as plt
from astropy import constants as const
from astropy import units as u
import plotly.graph_objects as go

##   1.   Generalización:
Implemente un código que resuelva el problema diferencial de las ecuaciones de movimiento utilizando un método Runge-Kutta de orden 4. El algoritmo debe ser lo suficientemente general para poder incluír un número arbitrario de partículas y las condiciones deben ser leídas de un archivo.






1.   Primero, se crea la clase principal para cada cuerpo



In [40]:
class Astrobject:
  def __init__(
      self,
      pos = np.zeros(3) * u.au, 
      vel = np.zeros(3) * u.au/ u.year,
      mass=1. * u.M_sun
  ):
    
    self.pos= pos
    self.vel = vel
    assert (mass > 0) 
    self.mass = mass
    self.dpos, self.dvel = self._initzeros() 

  def _initzeros(self):
    return ([np.zeros(3)* u.au, np.zeros(3) * u.au/ u.year])

  def acc(self, mass, distance): #ODE 
    up = const.G * mass * distance
    down = (np.linalg.norm(distance)) ** 3
    return (-up/down)

  def add_interaction(self, other): #Rudge Kuta 4 Implementation
    orbit_mass = other.mass 
    distance = (self.pos - other.pos).to(u.au)
    k1 = self.vel * dt
    vk1 = self.acc(orbit_mass, distance) * dt
    k2 = (self.vel + (vk1/2)) * dt
    vk2 = self.acc(orbit_mass, distance + (k1/2)) * dt
    k3 = (self.vel + (vk2/2)) * dt
    vk3 = self.acc(orbit_mass, distance + (k2/2)) * dt
    k4 = (self.vel + vk3) * dt
    vk4 = self.acc(orbit_mass, distance + k3) * dt
    self.dpos += (k1+ 2*k2 + 2*k3 + k4) / 6
    self.dvel += (vk1 + 2*vk2 + 2*vk3 + vk4) / 6

  def step(self):
    self.pos += self.dpos
    self.vel += self.dvel
    self.dpos, self.dvel = self._initzeros()

    return self.pos, self.vel


2.   Creación de la función que guarda un arreglo de clases para cada cuerpo



In [3]:
def nbodies(bd, du, vu, mu): #bd debe tener las unidades asignadas según el dato importado, además se colocan las unidades de posición , velocidad y masa para transformar
  bodies = np.array([Astrobject((i[0:3]*du).to(u.au),(i[3:6]*vu).to(u.au/ u.year), (i[6]*mu).to(u.M_sun)) for i in bd]) #Crea la clase para cada objeto con las unidades UA Years SolarMass
  return (bodies)



3.   Función del main loop



In [54]:
def astroloop(bodies, time):
  N = np.shape(bodies)[0] 
  bodiespos= np.zeros((N, time, 3))
  bodiesvel= np.zeros((N, time, 3))
  for t in range(time):
    for j in range(1, N):
      bodies[j].add_interaction(bodies[0])
    for l in range(N):
      bodiespos[l,t], bodiesvel[l,t] = bodies[l].step()
  return (bodiespos, bodiesvel)



4.   Función de graficación



In [42]:
def astroplotter(bodiespos, colors, labels): #Previamente debe definir el arreglo de colores y etiquetas
  fig = go.Figure()
  for t in range(np.shape(bodiespos)[0]):
    fig.add_trace(go.Scatter3d(
        x = bodiespos[t,:,0],
        y = bodiespos[t,:,1],
        z = bodiespos[t,:,2],
        marker= dict(
            size = 2,
            color= colors[t]),
        name = labels[t]))
  fig.show()

## 2.   Simulación sistema Sol-Tierra:
Con el fin de probar el código implementado, utilice los datos iniciales para el sistema Sol-Tierra dados en el archivo sun_earth.dat y grafique el comportamiento del sistema a lo largo de algunos años. Compruebe que la orbita no se comporta a la forma de una espiral.





1.   Cargar los datos



In [55]:
sun_earth = np.loadtxt("sun_earth.csv", delimiter=',')
sun_earth

array([[0.00000000e+00, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
        0.00000000e+00, 0.00000000e+00, 1.98855000e+30],
       [1.49598261e+11, 0.00000000e+00, 0.00000000e+00, 0.00000000e+00,
        2.97800000e+04, 0.00000000e+00, 5.97219000e+24]])


2.   Crear los objetos de los datos



In [56]:
bodies = nbodies(sun_earth, u.m, u.m/u.s, u.kg)
np.shape(bodies)

(2,)

3.   Integrar y guardar los valores de posición y velocidad

In [57]:
dt = (1 * u.d).to(u.year) 
time = int (((5*u.year)/dt).value)

In [58]:
bodiespos, bodiesvel = astroloop(bodies, time)



4.   Graficar



In [59]:
colors=['red', 'blue']
labels=['Sun', 'Earth']
astroplotter(bodiespos, colors, labels)

## 3.   Aseguramiento de Convergencia:
Con el fin de asegurar la convergencia del algoritmo, implemente una rutina dentro del programa que calcule la energía total del sistema de N-partículas. Evalue el comportamiento de la energía a lo largo de la evolución y grafique para comprobar si existe algún cambio significativo. ¿El comportamiento mejora o empeora al modificar el paso de la integración?



## 4.   Simulación Sistema estrellas alrededor de SgrA*:
Ahora utilice su código para estudiar la evolución del sistema de 13 estrellas $SO$ moviendose alrededor del agujero negro supermasivo $SgrA*$, proporcionado en el archivo SOstars.dat. Verifique también el comportamiento de la energía del sistema de 13+1 partículas. Grafique las orbitas de estas estrellas a lo largo de un periodo de 100 años.






1.   Cargar los datos



In [11]:
sgtastar = np.loadtxt('sgrAstar.csv', delimiter=',')
sgtastar

array([[ 0.00000e+00,  0.00000e+00,  0.00000e+00,  0.00000e+00,
         0.00000e+00,  0.00000e+00,  4.30000e+06],
       [-1.49438e-01,  6.83670e-02, -1.02779e-01,  1.87500e-03,
        -3.47500e-02, -3.57000e-02,  1.00000e+00],
       [-2.89880e-02,  1.64717e-01,  1.34333e-01, -1.13250e-02,
        -5.40000e-03,  4.37500e-03,  1.00000e+00],
       [ 1.41419e-01,  1.01052e-01, -4.08425e-01,  1.90500e-02,
         5.10000e-03,  3.10750e-02,  1.00000e+00],
       [ 2.59620e-01, -1.38803e-01,  3.08951e-01,  1.87000e-02,
        -1.69000e-02,  2.70000e+01,  1.00000e+00],
       [ 1.70643e-01, -2.63284e-01, -3.45612e-01,  3.85000e-03,
        -1.48750e-02,  2.98750e-02,  1.00000e+00],
       [ 1.04908e-01, -4.06364e-01,  4.41133e-01, -5.40000e-03,
         1.92500e-03,  2.38250e-02,  1.00000e+00],
       [-3.34829e-01,  3.86242e-01,  9.34040e-02,  1.40000e-03,
        -1.15750e-02, -2.04250e-02,  1.00000e+00],
       [ 1.91074e-01,  1.72231e-01, -6.31030e-02, -1.95500e-02,
        -1.56250

2.   Crear el arreglo de objectos de los datos



In [60]:
bodies = nbodies(sgtastar, np.tan(1*u.arcsec)*8*u.kpc, np.tan(1*u.arcsec)*8*u.kpc/u.year, u.M_sun)
np.shape(bodies)

(14,)

In [64]:
dt = (5 * u.d).to(u.year) 
time = int (((100*u.year)/dt).value)

In [65]:
bodiespos, bodiesvel = astroloop(bodies, time)

In [73]:
colors=['black', 'indigo', 'bisque', 'red', 'blue', 'magenta', 'cyan', 'green', 'tomato', 'firebrick', 'gold', 'azure', 'lavender', 'lavenderblush']
labels=['Sgr A*']
labels += ['Star %d' % (i+1) for i in range(len(sgtastar) - 1)]
astroplotter(bodiespos, colors, labels)